In [6]:
import nltk
import numpy as np
from nltk.stem.snowball import SnowballStemmer
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Godel\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [7]:
import os
import math
import heapq
from collections import defaultdict, deque
from nltk.tokenize import RegexpTokenizer
import re

In [8]:
stemmer = SnowballStemmer("spanish")

with open('stoplist.txt', 'r') as file:
    stoplist = file.read().splitlines()
stoplist += ['.', ',', ';', ':', '!', '?', '¿', '¡', '(', ')', '[', ']', '{', '}', '"', "'", '``', "''","111âº","111º","«","»"]

def preprocesamiento(text):
    # Reemplazar siglas con puntos por la misma sigla sin puntos
    text = re.sub(r'\b(\w\.)+\b', lambda match: match.group(0).replace('.', ''), text)
    # Separar números de las palabras
    text = re.sub(r'(\d+)', r' \1 ', text)
    # Tokenizar, tratando la puntuación como tokens separados
    tokenizer = RegexpTokenizer(r'\w+|\$[\d\.]+|\S+')
    text = tokenizer.tokenize(text)
    # Normalizar: convertir a minúsculas
    text = [word.lower() for word in text]
    # Eliminar signos de puntuación
    text = [re.sub(r'[^\w\s]', '', word) for word in text]
    # Filtrar stopwords
    text = [word for word in text if word not in stoplist]
    # Filtrar números
    text = [word for word in text if not word.isdigit()]
    # Stemming
    text = [stemmer.stem(word) for word in text]
    # Unir los tokens en una cadena y eliminar espacios extra
    text = ' '.join(text).replace('  ', ' ') ####################
    return text

#ejemplo 
query = "riCarDo,julio imaginemos.pero y la O.N.U, el GraN mano brimstone2 5.43"

# convertir a string
#query = ' '.join(query)

print(preprocesamiento(query))

# construcción de un tipo de índice invertido en memoria ram
textos = ["libro1.txt","libro2.txt","libro3.txt","libro4.txt","libro5.txt","libro6.txt"]
textos_procesados = []
indice = {} # para que sirve esto?  # para saber cuantas veces aparece una palabra en cada texto
for file_name in textos:
  file = open('docs/'+file_name, encoding = 'utf-8')
  texto = file.read().rstrip()
  texto = preprocesamiento(texto)  
  textos_procesados.append(texto)
  for word in texto.split():
    if word not in indice:
      indice[word] = [0,0,0,0,0,0]
    indice[word][textos.index(file_name)] += 1
    #ordenar por termino
  indice = dict(sorted(indice.items()))
  
#pasar libros sin procesar a un diccionario
librillos_sin_procesar ={}
i = 1
for file_name in textos:
  file = open('docs/'+file_name, encoding='utf-8')
  texto = file.read().rstrip()
  librillos_sin_procesar[i] = texto
  i += 1
  

#librillos_sin_procesar

#indice

ricard juli imagin onu man brimston


In [9]:
import os
import math
from collections import defaultdict, deque
import re

# Preprocesamiento: Tokenización, Stopword Removal, Stemming
stemmer = SnowballStemmer("spanish")

with open('stoplist.txt', 'r') as file:
    stoplist = file.read().splitlines()
stoplist += ['.', ',', ';', ':', '!', '?', '¿', '¡', '(', ')', '[', ']', '{', '}', '"', "'", '``', "''","111âº","111º","«","»"]

def preprocesamiento(text):
    # Reemplazar siglas con puntos por la misma sigla sin puntos
    text = re.sub(r'\b(\w\.)+\b', lambda match: match.group(0).replace('.', ''), text)
    # Separar números de las palabras
    text = re.sub(r'(\d+)', r' \1 ', text)
    # Tokenizar, tratando la puntuación como tokens separados
    tokenizer = RegexpTokenizer(r'\w+|\$[\d\.]+|\S+')
    text = tokenizer.tokenize(text)
    # Normalizar: convertir a minúsculas
    text = [word.lower() for word in text]
    # Eliminar signos de puntuación
    text = [re.sub(r'[^\w\s]', '', word) for word in text]
    # Filtrar stopwords
    text = [word for word in text if word not in stoplist]
    # Filtrar números
    text = [word for word in text if not word.isdigit()]
    # Stemming
    text = [stemmer.stem(word) for word in text]
    # Unir los tokens en una cadena y eliminar espacios extra
    text = ' '.join(text)
    return text

# Construcción del Índice Invertido usando SPIMI
def spimi_invert(token_stream, block_size):
    output_file = open(f"block_{spimi_invert.block_count}.txt", "w")
    spimi_invert.block_count += 1
    
    dictionary = defaultdict(dict)
    
    while token_stream:
        token, doc_id = token_stream.popleft()
        if doc_id not in dictionary[token]:
            dictionary[token][doc_id] = 0
        dictionary[token][doc_id] += 1
        
        if len(dictionary) > block_size:
            break
    
    sorted_terms = sorted(dictionary.items())
    for term, postings in sorted_terms:
        postings_str = " ".join([f"{doc_id}:{tf}" for doc_id, tf in postings.items()])
        output_file.write(f"{term} {postings_str}\n")
    output_file.close()

    return output_file.name

spimi_invert.block_count = 0

def parse_docs(documents):
    token_stream = deque()
    for doc_id, text in documents.items():
        tokens = preprocesamiento(text).split()
        for token in tokens:
            token_stream.append((token, doc_id))
    return token_stream

def merge_blocks(block_files, total_docs):
    term_dict = defaultdict(dict)
    doc_freq = defaultdict(int)

    for block_file in block_files:
        with open(block_file, "r") as f:
            for line in f:
                term, postings = line.strip().split(' ', 1)
                postings_list = postings.split()
                for posting in postings_list:
                    doc_id, tf = posting.split(':')
                    doc_id = int(doc_id)
                    tf = int(tf)
                    if doc_id not in term_dict[term]:
                        term_dict[term][doc_id] = 0
                    term_dict[term][doc_id] += tf
                    doc_freq[term] += 1

    sorted_terms = sorted(term_dict.items())
    with open("final_index.txt", "w") as f:
        for term, postings in sorted_terms:
            if doc_freq[term] == 0: # si no aparece en ningun documento, idf = 0
                idf = 0
            else:
                idf = math.log10(1 + (total_docs / doc_freq[term]))
            postings_str = " ".join([f"{doc_id}:{round((1 + math.log10(tf)) * idf,2)}" for doc_id, tf in postings.items()])
            f.write(f"{term} {postings_str}\n")

def build_index(documents, block_size):
    total_docs = len(documents)
    token_stream = parse_docs(documents)
    block_files = []
    while token_stream:
        block_file = spimi_invert(token_stream, block_size)
        block_files.append(block_file)
    merge_blocks(block_files, total_docs)

# Ejemplo de uso
documents = {
    1: "El rápido zorro marrón salta sobre el perro perezoso",
    2: "Un zorro es un animal astuto",
    3: "El perro es el mejor amigo del hombre",
    4: "El perro y el zorro son amigos",
    5: "El hombre y el zorro son enemigos",
    6: "El gato es enemigo del perro",
    7: "El gato y el zorro son amigos",
    8: "El gato es astuto",
    9: "El gato es rápido",
    10: "El perro es fiel"
}

for doc_id, text in documents.items():
    documents[doc_id] = preprocesamiento(text)
    print(f"Documento {doc_id}: {documents[doc_id]}")

textos = ["libro1.txt","libro2.txt","libro3.txt","libro4.txt","libro5.txt","libro6.txt"]
textos_procesados = []
indice = {} # para que sirve esto?  # para saber cuantas veces aparece una palabra en cada texto
librillos ={}
i = 1
for file_name in textos:
  file = open('docs/'+file_name,encoding='utf-8')
  texto = file.read().rstrip()
  texto = preprocesamiento(texto)
  textos_procesados.append(texto)
  librillos[i] = texto
  i += 1

for doc_id, text in librillos.items():
    librillos[doc_id] = preprocesamiento(text)
    print(f"Documento {doc_id}: {text}")

import pandas as pd

dataton = pd.read_csv('df_total.csv')
#solo guardar 100 documentos
dataton = dataton.head(25)

# crear diccionario de documentos
documentos_sin_procesar = {}
for i in range(len(dataton)):
    documentos_sin_procesar[i] = dataton['news'][i]
    
documentos_procesados = {}
for doc_id, text in documentos_sin_procesar.items():
    documentos_procesados[doc_id] = preprocesamiento(text)

#build_index(documents, 7)
#build_index(librillos, 500)
build_index(documentos_procesados, 800)

Documento 1: rap zorr marron salt perr perez
Documento 2: zorr animal astut
Documento 3: perr amig hombr
Documento 4: perr zorr amig
Documento 5: hombr zorr enemig
Documento 6: gat enemig perr
Documento 7: gat zorr amig
Documento 8: gat astut
Documento 9: gat rap
Documento 10: perr fiel
Documento 1: obra comienz notici celebr º cumpleañ bilb bolson comarc   bilb fiest ten motiv principal part ultim viaj  product dese termin dias paz tranquil  mag gandalf  amig bilb inform decision hobbit  tambien acud fiest  discurs pronunci bilb  pus anill magic desaparec sorprend hobbits  gandalf  sab acab bilb  encontr bolson cerr alli pequeñ discusion el  neg dej anill rest herenci sobrin frod   mag acab convenc bilb part   dud ocasion anill  gandalf busc inform el  inform frod guard toqu  veint años despues  gandalf regres bolson cerr frod hab descubiert anill  trat rey isildur arnor hab arrebat señor oscur sauron años despues hab encontr criatur gollum hab perd rio anduin desastr camp gladi  qued

In [10]:
# Cargar el índice invertido
index = defaultdict(dict)
with open("final_index.txt", "r") as f:
    for line in f:
        term, postings = line.strip().split(' ', 1)
        postings_list = postings.split()
        for posting in postings_list:
            doc_id, tfidf = posting.split(':')
            doc_id = int(doc_id)
            tfidf = float(tfidf)
            if doc_id not in index[term]:
                index[term][doc_id] = 0
            index[term][doc_id] += tfidf
            
# Calcular la norma de los documentos y guardarlo en un diccionario
def calculate_norms(index):
    norms = defaultdict(float)
    for term, postings in index.items():
        for doc_id, tfidf in postings.items():
            norms[doc_id] += tfidf ** 2
    for doc_id in norms:
        norms[doc_id] = math.sqrt(norms[doc_id])
    return norms

norms = calculate_norms(index)

print(norms)
index

defaultdict(<class 'float'>, {22: 18.202947563512897, 12: 17.153632268414754, 1: 11.878901464361087, 13: 14.655459733491815, 0: 8.869571579281606, 2: 12.935180709986236, 4: 18.027517854657642, 11: 18.511653086637075, 16: 10.240688453419526, 6: 15.855986251255398, 19: 10.240439443695763, 15: 9.53306876089751, 23: 16.64149933149054, 3: 14.462067625343206, 5: 8.965204961404954, 24: 20.85737279716695, 8: 16.579626051271486, 18: 18.92416973079665, 20: 16.426661255410366, 14: 12.057441685531803, 21: 15.63177852964915, 7: 7.516787877810575, 9: 7.982793997091496, 10: 12.417109164374775, 17: 8.330228088113795})


defaultdict(dict,
            {'abacum': {22: 1.41},
             'abastec': {12: 1.41},
             'abiert': {1: 0.97, 13: 0.97, 22: 0.97},
             'abord': {22: 1.41},
             'abre': {0: 1.41},
             'abrir': {2: 1.41},
             'aca': {0: 1.41},
             'acab': {13: 1.41},
             'acced': {4: 1.26, 11: 1.26, 16: 0.97},
             'acces': {4: 0.93,
              6: 0.71,
              12: 0.71,
              16: 0.93,
              19: 0.71,
              22: 0.71},
             'accion': {1: 0.93, 6: 0.93, 12: 0.71, 15: 1.05, 23: 0.71},
             'accionarial': {11: 1.41},
             'aceit': {3: 1.41},
             'acel': {5: 0.86, 22: 0.86, 23: 1.27, 24: 1.12},
             'acerc': {4: 1.13, 8: 1.13},
             'acomet': {11: 1.41},
             'acompañ': {11: 1.43, 18: 0.97, 22: 0.97},
             'acondicion': {24: 1.41},
             'aconsej': {12: 1.41},
             'acopl': {20: 1.41},
             'acord': {18: 1.41},
     

In [14]:
import time

def cosine_similarity(query, index, norms, k): # search
    start = time.time()
    scores = defaultdict(float)
    query_tokens = preprocesamiento(query).split()
    query_tf = defaultdict(int)
    for token in query_tokens:
        query_tf[token] += 1
    query_vector = {token: 1 + math.log10(tf) for token, tf in query_tf.items() if token in index}
    
    query_norm = math.sqrt(sum((1 + math.log10(tf))**2 for tf in query_tf.values() if tf > 0))
    
    for token, weight in query_vector.items():
        if token in index:
            for doc_id, tfidf in index[token].items():
                scores[doc_id] += weight * tfidf
    
    for doc_id in scores:
        scores[doc_id] /= query_norm * norms[doc_id]
    result = sorted(scores.items(), key=lambda x: x[1], reverse=True)[:k]
    end = time.time()
    duration = end - start
    return result, duration

def retrieval_documents(result, docs):
    for doc_id, score in result:
        print(f"Documento {doc_id}: {docs[doc_id]}, Score: {score}")

#result = cosine_similarity("debido a la codicia desperto frodo sam ithilien", index, norms, 2)
#print(result)
#retrieval_documents(result, librillos_sin_procesar)


Query1 = "El pais de China y su cooperacion"
result, duration = cosine_similarity(Query1, index, norms, 3)
print(f'{result}, tiempo de la query: {duration} segundos')
retrieval_documents(result, documentos_sin_procesar)

[(15, 0.11204136094999165), (1, 0.08116701299689869), (20, 0.05658690581989944)], tiempo de la query: 0.0 segundos
Documento 15: JPMorgan dijo el lunes que los cambios regulatorios chinos eran un problema local más que global y que el banco seguía sobreponderado las acciones de los mercados emergentes.El banco dijo que si bien es probable que continúe la revisión de la regulación China evitaría cambios que causen un impacto en el crecimiento económico.Las acciones chinas sufrieron una gran liquidación la semana pasada con el índice referencial CSI300 registrando su peor mes en casi tres años luego de una serie de medidas regulatorias dirigidas a los sectores de educación superior tecnología y propiedad.Vemos el riesgo de más cambios regulatorios en China como un problema local más que global escribieron analistas de JPMorgan en una nota fechada el lunes.Dada la corrección sustancial en los segmentos de mercado afectados este riesgo parece estar ya descontado y podría disminuir a partir

In [12]:
cosine_similarity("por la muerte de gandalf",index,norms,2)

([], 0.0)

In [87]:
import pandas as pd

dataton = pd.read_csv('df_total.csv')
dataton.head()

Query1 = "El pais de China y su cooperacion"

# crear diccionario de documentos
documentos_sin_procesar = {}
for i in range(len(dataton)):
    documentos_sin_procesar[i] = dataton['news'][i]
    
documentos_procesados = {}
for doc_id, text in documentos_sin_procesar.items():
    documentos_procesados[doc_id] = preprocesamiento(text)
    
documentos_procesados

{0: 'for banc articul empresarial desarroll sosten director sostenibil client global bbva colombi andres garc asegur import entend sostenibil asoci mayor cost concept negoci sosten impact imagin garc ret mas import cambi prioridad compit si necesari cas trat manten priorid ambicion negoci mas sosten ret enorm coyuntur sostenibil abre oportun mejor fuent financi agreg direct argument jueg aca tem rentabil negoci particul tem viabil mund negoci mund fisic general conoc ademas riesg fisic transicion asoci cambi climat inclusion social desarroll real estan ahi dej aspect paralel respons social corpor adn estrategi negoci logr impuls proyect especif estan inclu aspir conclu ',
 1: 'regul valor chin doming busc cooper mas estrech par estadounidens apoy sal bols extranjer supervisor estadounidens endurec exigent divulg inform empres chin expres preocup med pekin comision regul valor chin csrc comunic tom not requisit comision valor unid sec empres chin ambas part deb manten espiritu respet mu

In [21]:
documentos_sin_procesar

{0: 'Durante el foro La banca articulador empresarial para el desarrollo sostenible el director de sostenibilidad y clientes globales de BBVA en Colombia Andrés García aseguró que es importante entender que la sostenibilidad no la podemos asociar a mayores costos. Yo creo que el no tener un concepto de negocio sostenible puede tener un mayor impacto de lo que imaginamos.Para García el reto más importante es no cambiar prioridades ni que compitan entre sí necesariamente. En muchos de los casos se debe tratar de mantener la prioridad en cuanto a la ambición de negocios más sostenibles un reto enorme por la coyuntura. La sostenibilidad nos abre oportunidades a mejores fuentes de financiamiento agregó.El directivo argumentó que lo que se encuentra en juego acá no es un tema de rentabilidad o de negocios en particular es un tema de viabilidad del mundo de los negocios y del mundo físico en general como lo conocemos. Además los riesgos físicos y de transición asociados al cambio climático y 

In [9]:
resultado = cosine_similarity(Query1, index, norms, 3)
retrieval_documents(resultado, documentos_sin_procesar)

Documento 1: El regulador de valores de China dijo el domingo que buscará una cooperación más estrecha con su par estadounidense y que apoyará las salidas a bolsa en el extranjero luego de que supervisores estadounidenses endurecieron las exigencias de divulgación de información para las empresas chinas y expresaron preocupación por medidas de Pekín.La Comisión Reguladora de Valores de China CSRC dijo en un comunicado que tomó nota de los nuevos requisitos de la Comisión de Valores de Estados Unidos SEC para las empresas chinas y que ambas partes deberían mantener el espíritu de respeto mutuo y reforzar las comunicaciones sobre la regulación.La CSRC siempre ha estado abierta a que las empresas elijan dónde salir a bolsa y la política nacional básica de China de avanzar en la reforma y la apertura es inquebrantable y la apertura financiera al mundo exterior continuará dijo en su sitio web.La SEC había dicho el viernes que exigirá a las compañías chinas que revelen la incertidumbre sobre